In [ ]:
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime as dt
import time

username = 'jizhaobridgeport@gmail.com'
password = '12345shift'

def login():
    rh.login(username, password)
def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = (today-datetime.timedelta(1)).strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        
        # Print the raw data to check
        print(f"Raw data for {stock}:")
        print(bs)
        
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        
        # Print calculations
        print("\nCalculations:")
        print(f"Center of Gravity: {last_day['center_gravity'].values[0]}")
        
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        print(f"Volatility Up 1: {last_day['vol_up1'].values[0]}")
        
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        print(f"Volatility Down 1: {last_day['vol_down1'].values[0]}")
        
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        print(f"Volatility Up 2: {last_day['vol_up2'].values[0]}")
        
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        print(f"Volatility Down 2: {last_day['vol_down2'].values[0]}")
        
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        print(f"Volatility Up 3: {last_day['vol_up3'].values[0]}")
        
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        print(f"Volatility Down 3: {last_day['vol_down3'].values[0]}")
        
        last_day['stop_loss'] = (last_day['vol_down2'] + last_day['vol_down3'])/2
        print(f"Initial Stop Loss: {last_day['stop_loss'].values[0]}")
        
        last_day['stop_loss_pct'] = (last_day['Close'] - last_day['stop_loss'])/last_day['Close']*100
        print(f"Initial Stop Loss Percentage: {last_day['stop_loss_pct'].values[0]}%")
        
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] + last_day['Close'][-1])/2
            print(f"Adjusted Stop Loss (because percentage > 3.5%): {last_day['stop_loss'].values[0]}")
        
        return last_day

    
    
def get_trailing_stop_percentage(stock):
    stop_price = get_stop(stock)['stop_loss'][0]
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

login()

sold_half = set()  # Track stocks that we have sold half of


while True:
    my_stocks = rh.build_holdings()
    df = pd.DataFrame(my_stocks).T
    df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
    stock = df1.index.tolist()
    all_data = pd.DataFrame()

    for ticker in stock:
        print(ticker)
        last_day = get_stop(ticker)
        all_data = pd.concat([all_data, last_day], axis=0)

    all_data = all_data[['stop_loss']]
    all_data1 = df1.merge(all_data, left_index=True, right_index=True)
    all_data1['price'] = all_data1['price'].astype(float)
    all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100

    import random
    x = random.random()
    y = float((x + 5) / 100)
    z = float((10 - x) / 100)
    all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
    all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
    all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)

    trailing_stop_percentages = {}
    for s in all_data1.index.tolist():
        trailing_stop_percentages[s] = get_trailing_stop_percentage(s)

    for s in all_data1.index.tolist():
        current_price = all_data1['price'][s]
        average_price = all_data1['average_buy_price'][s]
        quantity = float(all_data1['quantity'][s])
        trailing_stop_price = current_price * (1 - trailing_stop_percentages[s])
        loss_pct = (current_price - trailing_stop_price) / current_price * 100
        gain_pct = (current_price - average_price) / average_price * 100

        if current_price >= all_data1['target_price1'][s] and s not in sold_half:
            print(f"Would sell half of {s} at market price with a gain of {gain_pct:.2f}%.")
            sold_half.add(s)

        elif current_price >= all_data1['target_price2'][s]:
            print(f"Would sell all of {s} at market price with a gain of {gain_pct:.2f}%.")
        
        elif current_price <= trailing_stop_price:
            print(f"Trailing stop would be triggered for {s}, selling all at market price. Stop Price: ${trailing_stop_price:.2f}, Loss: {loss_pct:.2f}%.")

    time.sleep(3600)